In [1]:
from os import environ as ENV
from dotenv import load_dotenv
import datetime

import streamlit as st
import pyodbc
import pandas as pd
import altair as alt
alt.data_transformers.enable("vegafusion")

DataTransformerRegistry.enable('vegafusion')

In [2]:
def get_db_connection() -> pyodbc.Connection:
    """Returns a connection to database."""

    load_dotenv()
    conn_str = (f"DRIVER={{{ENV['DB_DRIVER']}}};SERVER={ENV['DB_HOST']};"
                f"PORT={ENV['DB_PORT']};DATABASE={ENV['DB_NAME']};"
                f"UID={ENV['DB_USER']};PWD={ENV['DB_PASSWORD']};Encrypt=no;")

    conn = pyodbc.connect(conn_str)

    return conn


def load_data() -> pd.DataFrame:
    """ Pulls all the transaction data from the S3 bucket. """
    conn = get_db_connection()

    query = """
    SELECT
        pr.*, p.*, c.*
    FROM
        gamma.plant_reading pr
    LEFT JOIN
        gamma.plant p
    ON pr.plant_id = p.plant_id
    LEFT JOIN
        gamma.city c
    ON p.city_id = c.city_id;
    """

    df_recordings = pd.read_sql(query, conn)
    df_recordings.set_index("reading_id")
    return df_recordings

In [3]:
load_dotenv()
data = load_data()
data

/var/folders/fr/kzms8z2x39l0r6skc7f8fm3h0000gp/T/ipykernel_64187/1118687527.py:31: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_recordings = pd.read_sql(query, conn)


reading_id  plant_id  botanist_id  temperature        last_watered  \
0               1         1            1           14 2025-09-25 13:51:41   
1               2         2            2           14 2025-09-25 14:58:34   
2               3         3            3           80 2025-09-25 13:58:19   
3               4         4            4           16 2025-09-25 14:56:07   
4               5         5            5           16 2025-09-25 13:57:08   
...           ...       ...          ...          ...                 ...   
18953       18954        41           42           17 2025-09-26 13:08:03   
18954       18955        42           43           11 2025-09-26 14:50:57   
18955       18956        43           44           14 2025-09-26 14:09:29   
18956       18957        47           48           16 2025-09-26 14:08:03   
18957       18958        44           45           14 2025-09-26 14:30:25   

       soil_moisture         recording_taken  plant_id  \
0              32.97 2025-09-26 09:28:06.098         1   
1              34.15 2025-09-26 09:28:04.689         2   
2              35.61 2025-09-26 09:28:05.186         3   
3              36.58 2025-09-26 09:28:06.053         4   
4              29.81 2025-09-26 09:28:05.664         5   
...              ...                     ...       ...   
18953          88.58 2025-09-26 16:19:04.792        41   
18954          92.45 2025-09-26 16:19:04.474        42   
18955          92.39 2025-09-26 16:19:05.963        43   
18956          92.49 2025-09-26 16:19:04.768        47   
18957          93.85 2025-09-26 16:19:05.284        44   

                      plant_name    lat    lang  city_id  \
0                  Venus flytrap  43.74  -11.51        1   
1                  Corpse flower  47.84  -48.71        2   
2             Rafflesia arnoldii -25.49  -36.13        3   
3               Black bat flower  63.37   46.40        4   
4                  Pitcher plant  82.89    0.63        5   
...                          ...    ...     ...      ...   
18953        Medinilla Magnifica -34.19  -78.70       42   
18954  Calliandra Haematocephala  83.92 -148.55       43   
18955     Zamioculcas Zamiifolia -82.18  -72.49       44   
18956             Crassula Ovata  15.80  148.99       48   
18957          Epipremnum Aureum -62.63   18.62       45   

                   scientific_name  city_id          city_name  \
0                             None        1          Stammside   
1                             None        2           Floshire   
2                             None        3          Dale City   
3                             None        4       West Tedboro   
4           'Sarracenia catesbaei'        5      North Felicia   
...                            ...      ...                ...   
18953        'Medinilla magnifica'       42       Kathrynville   
18954  'Calliandra haematocephala'       43          Gavinstad   
18955     'Zamioculcas zamiifolia'       44  Lake Norbertstead   
18956             'Crassula ovata'       48           Ginaberg   
18957          'Epipremnum aureum'       45          Joanyland   

                  state_name  
0                    Albania  
1             American Samoa  
2                 Mozambique  
3                     Taiwan  
4      Saint Kitts and Nevis  
...                      ...  
18953                  Macao  
18954                 Jersey  
18955              Greenland  
18956                   Togo  
18957    Antigua and Barbuda  

[18958 rows x 16 columns]

In [4]:
last_watered_df = data[['last_watered', 'plant_name', 'soil_moisture', 'temperature']]
last_watered_df

last_watered                 plant_name  soil_moisture  \
0     2025-09-25 13:51:41              Venus flytrap          32.97   
1     2025-09-25 14:58:34              Corpse flower          34.15   
2     2025-09-25 13:58:19         Rafflesia arnoldii          35.61   
3     2025-09-25 14:56:07           Black bat flower          36.58   
4     2025-09-25 13:57:08              Pitcher plant          29.81   
...                   ...                        ...            ...   
18953 2025-09-26 13:08:03        Medinilla Magnifica          88.58   
18954 2025-09-26 14:50:57  Calliandra Haematocephala          92.45   
18955 2025-09-26 14:09:29     Zamioculcas Zamiifolia          92.39   
18956 2025-09-26 14:08:03             Crassula Ovata          92.49   
18957 2025-09-26 14:30:25          Epipremnum Aureum          93.85   

       temperature  
0               14  
1               14  
2               80  
3               16  
4               16  
...            ...  
18953           17  
18954           11  
18955           14  
18956           16  
18957           14  

[18958 rows x 4 columns]

In [5]:
data.sort_values(by=['plant_name', 'last_watered'])

reading_id  plant_id  botanist_id  temperature        last_watered  \
31             32        32           33           12 2025-09-25 14:18:52   
75             76        32           33           12 2025-09-25 14:18:52   
122           123        32           33           12 2025-09-25 14:18:52   
168           169        32           33           12 2025-09-25 14:18:52   
214           215        32           33           12 2025-09-25 14:18:52   
...           ...       ...          ...          ...                 ...   
18767       18768        43           44           14 2025-09-26 14:09:29   
18814       18815        43           44           14 2025-09-26 14:09:29   
18861       18862        43           44           14 2025-09-26 14:09:29   
18908       18909        43           44           14 2025-09-26 14:09:29   
18955       18956        43           44           14 2025-09-26 14:09:29   

       soil_moisture         recording_taken  plant_id  \
31             32.53 2025-09-26 09:28:04.944        32   
75             35.14 2025-09-26 09:29:04.364        32   
122            32.08 2025-09-26 09:30:05.028        32   
168            35.15 2025-09-26 09:31:05.359        32   
214            33.72 2025-09-26 09:32:04.767        32   
...              ...                     ...       ...   
18767          92.97 2025-09-26 16:15:04.561        43   
18814          92.89 2025-09-26 16:16:04.768        43   
18861          92.43 2025-09-26 16:17:05.828        43   
18908          92.71 2025-09-26 16:18:05.847        43   
18955          92.39 2025-09-26 16:19:05.963        43   

                   plant_name    lat   lang  city_id  \
31       Aglaonema Commutatum -59.67  22.17       33   
75       Aglaonema Commutatum -59.67  22.17       33   
122      Aglaonema Commutatum -59.67  22.17       33   
168      Aglaonema Commutatum -59.67  22.17       33   
214      Aglaonema Commutatum -59.67  22.17       33   
...                       ...    ...    ...      ...   
18767  Zamioculcas Zamiifolia -82.18 -72.49       44   
18814  Zamioculcas Zamiifolia -82.18 -72.49       44   
18861  Zamioculcas Zamiifolia -82.18 -72.49       44   
18908  Zamioculcas Zamiifolia -82.18 -72.49       44   
18955  Zamioculcas Zamiifolia -82.18 -72.49       44   

                scientific_name  city_id          city_name      state_name  
31       'Aglaonema commutatum'       33         New Danika  Western Sahara  
75       'Aglaonema commutatum'       33         New Danika  Western Sahara  
122      'Aglaonema commutatum'       33         New Danika  Western Sahara  
168      'Aglaonema commutatum'       33         New Danika  Western Sahara  
214      'Aglaonema commutatum'       33         New Danika  Western Sahara  
...                         ...      ...                ...             ...  
18767  'Zamioculcas zamiifolia'       44  Lake Norbertstead       Greenland  
18814  'Zamioculcas zamiifolia'       44  Lake Norbertstead       Greenland  
18861  'Zamioculcas zamiifolia'       44  Lake Norbertstead       Greenland  
18908  'Zamioculcas zamiifolia'       44  Lake Norbertstead       Greenland  
18955  'Zamioculcas zamiifolia'       44  Lake Norbertstead       Greenland  

[18958 rows x 16 columns]

In [6]:
last_watered_df = last_watered_df.drop_duplicates()
last_watered_df

last_watered                 plant_name  soil_moisture  \
0     2025-09-25 13:51:41              Venus flytrap          32.97   
1     2025-09-25 14:58:34              Corpse flower          34.15   
2     2025-09-25 13:58:19         Rafflesia arnoldii          35.61   
3     2025-09-25 14:56:07           Black bat flower          36.58   
4     2025-09-25 13:57:08              Pitcher plant          29.81   
...                   ...                        ...            ...   
18953 2025-09-26 13:08:03        Medinilla Magnifica          88.58   
18954 2025-09-26 14:50:57  Calliandra Haematocephala          92.45   
18955 2025-09-26 14:09:29     Zamioculcas Zamiifolia          92.39   
18956 2025-09-26 14:08:03             Crassula Ovata          92.49   
18957 2025-09-26 14:30:25          Epipremnum Aureum          93.85   

       temperature  
0               14  
1               14  
2               80  
3               16  
4               16  
...            ...  
18953           17  
18954           11  
18955           14  
18956           16  
18957           14  

[17897 rows x 4 columns]

In [7]:
def format_timedelta(delta: datetime.timedelta) -> str:
    """ Formats timedelta into a more readable format. """
    seconds_in_day = 86400
    seconds_in_hour = 3600
    seconds_in_minute = 60

    seconds = int(delta.total_seconds())

    days = seconds // seconds_in_day
    hours = (seconds % seconds_in_day) // seconds_in_hour
    minutes = (seconds % seconds_in_hour) // seconds_in_minute

    return f'{days} days, {hours} hours, {minutes} minutes'

In [11]:
now = datetime.datetime.now()
last_watered_df['hours_since_watered'] = (now - last_watered_df['last_watered']).dt.total_seconds() / 3600
last_watered_df['time_since_watered_formatted'] = (
    now - last_watered_df['last_watered']).apply(format_timedelta)
last_watered_df

/var/folders/fr/kzms8z2x39l0r6skc7f8fm3h0000gp/T/ipykernel_64187/3715007286.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  last_watered_df['hours_since_watered'] = (now - last_watered_df['last_watered']).dt.total_seconds() / 3600
/var/folders/fr/kzms8z2x39l0r6skc7f8fm3h0000gp/T/ipykernel_64187/3715007286.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  last_watered_df['time_since_watered_formatted'] = (


last_watered                 plant_name  soil_moisture  \
0     2025-09-25 13:51:41              Venus flytrap          32.97   
1     2025-09-25 14:58:34              Corpse flower          34.15   
2     2025-09-25 13:58:19         Rafflesia arnoldii          35.61   
3     2025-09-25 14:56:07           Black bat flower          36.58   
4     2025-09-25 13:57:08              Pitcher plant          29.81   
...                   ...                        ...            ...   
18953 2025-09-26 13:08:03        Medinilla Magnifica          88.58   
18954 2025-09-26 14:50:57  Calliandra Haematocephala          92.45   
18955 2025-09-26 14:09:29     Zamioculcas Zamiifolia          92.39   
18956 2025-09-26 14:08:03             Crassula Ovata          92.49   
18957 2025-09-26 14:30:25          Epipremnum Aureum          93.85   

       temperature  hours_since_watered time_since_watered_formatted  
0               14            27.471909  1 days, 3 hours, 28 minutes  
1               14            26.357187  1 days, 2 hours, 21 minutes  
2               80            27.361354  1 days, 3 hours, 21 minutes  
3               16            26.398020  1 days, 2 hours, 23 minutes  
4               16            27.381076  1 days, 3 hours, 22 minutes  
...            ...                  ...                          ...  
18953           17             4.199131  0 days, 4 hours, 11 minutes  
18954           11             2.484131  0 days, 2 hours, 29 minutes  
18955           14             3.175242  0 days, 3 hours, 10 minutes  
18956           16             3.199131  0 days, 3 hours, 11 minutes  
18957           14             2.826354  0 days, 2 hours, 49 minutes  

[17897 rows x 6 columns]

In [12]:
last_watered_df.loc[last_watered_df['soil_moisture'] < 0, 'soil_moisture'] = None

In [16]:
last_watered_df

last_watered                 plant_name  soil_moisture  \
0     2025-09-25 13:51:41              Venus flytrap          32.97   
1     2025-09-25 14:58:34              Corpse flower          34.15   
2     2025-09-25 13:58:19         Rafflesia arnoldii          35.61   
3     2025-09-25 14:56:07           Black bat flower          36.58   
4     2025-09-25 13:57:08              Pitcher plant          29.81   
...                   ...                        ...            ...   
18953 2025-09-26 13:08:03        Medinilla Magnifica          88.58   
18954 2025-09-26 14:50:57  Calliandra Haematocephala          92.45   
18955 2025-09-26 14:09:29     Zamioculcas Zamiifolia          92.39   
18956 2025-09-26 14:08:03             Crassula Ovata          92.49   
18957 2025-09-26 14:30:25          Epipremnum Aureum          93.85   

       temperature  hours_since_watered time_since_watered_formatted  
0               14            27.471909  1 days, 3 hours, 28 minutes  
1               14            26.357187  1 days, 2 hours, 21 minutes  
2               80            27.361354  1 days, 3 hours, 21 minutes  
3               16            26.398020  1 days, 2 hours, 23 minutes  
4               16            27.381076  1 days, 3 hours, 22 minutes  
...            ...                  ...                          ...  
18953           17             4.199131  0 days, 4 hours, 11 minutes  
18954           11             2.484131  0 days, 2 hours, 29 minutes  
18955           14             3.175242  0 days, 3 hours, 10 minutes  
18956           16             3.199131  0 days, 3 hours, 11 minutes  
18957           14             2.826354  0 days, 2 hours, 49 minutes  

[17897 rows x 6 columns]

In [ ]:

alt.Chart(last_watered_df, title='Time since each plant was watered').mark_bar().encode(
    y=alt.Y('plant_name', title='Plant Name',
            axis=alt.Axis(labelLimit=200), sort='-x'),
    x=alt.X('hours_since_watered', title='Hours since watered'),
    tooltip=[alt.Tooltip('time_since_watered_formatted', title='Time since plant was watered'),
             alt.Tooltip('soil_moisture', title='Soil moisture'),
             alt.Tooltip('temperature', title='Temperature')]
)

alt.Chart(...)